# MIPANSUSUSU 

## Contents
- [Packages](#section1)
- [Datasets Cleaning](#section2)
    - [HDB Resale 2020](#subsection2.1)
    - [MRT Coordinates](#subsection2.2)
    - [Mall Coordinates](#subsection2.3)
    - [BusStop Coordinates](#subsection2.4)
    - [Import All Other Relevant Datasets](#subsection2.5)
- [General Functions](#section3)

## Packages<a id="section2"></a>

In [1]:
import json
import requests
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import urllib  

## Datasets Cleaning<a id="section1"></a>

We first begin by cleaning raw data sets in order to consolidate related data, as well as process data for later data visualisation and data processing.

<div class="alert alert-block alert-success">
<b>List of Key Datasets:</b> 
The Key Datasets we will be using are summarised below (alongside links to online data files if applicable)
  <li><b><a href="https://data.gov.sg/dataset/resale-flat-prices">HDB Resale Data</a></b>: Resale price, town, blk, street_name, postal code, longitude and latitude of HDB blocks</li>
  <li><b>Malls</b>: Shopping Mall Names, region, longitude and latitude</li>
  <li><b>MRT</b>: MRT locations, longitude and latitude</li>
  <li><b><a href="https://github.com/cheeaun/busrouter-sg/blob/master/data/3/stops.onemap.json">Buses</a></b>: BusStop Numbers, longitude and latitude</li>
</div> 


<a href="https://docs.onemap.sg/#search">OneMap API</a> was utilised in mapping corresponding latitude and longitude data to respective locations.

Due to the length of time taken to query onemap's API to attain geolocation data, we have prerun the queries and exported the data into a csv file for any later data processing and visualisation. The below variable has been set to 'False' to prevent rerunning of those specific queries when restarting the kernel

If necessary we converted json files with raw data to csv for easier processing through an <a href="https://www.convertcsv.com/json-to-csv.htm">online converting site</a>.

In [2]:
rerun = True

### HDB Resale 2020 gov.sg<a id="subsection2.1"></a>

In [3]:
#Query to gov.sg site to access 2017-2020 json file and convert to python object
query_string='https://data.gov.sg/api/action/datastore_search?resource_id=42ff9cfe-abe5-4b54-beda-c88f9bb438ee&limit=77895'
resp = requests.get(query_string)

#Convert JSON into Python Object 
data = json.loads(resp.content)
hdb_price_dict_records = data['result']['records']

In [4]:
town = []
flat_type = []
flat_model = []
floor_area_sqm = []
street_name = []
resale_price = []
month = []
remaining_lease = []
lease_commence_date = []
storey_range = []
_id = []
block = []

for i in range(0, len(hdb_price_dict_records)):
    town.append(hdb_price_dict_records[i]['town'])
    flat_type.append(hdb_price_dict_records[i]['flat_type'])
    flat_model.append(hdb_price_dict_records[i]['flat_model'])
    floor_area_sqm.append(hdb_price_dict_records[i]['floor_area_sqm'])
    street_name.append(hdb_price_dict_records[i]['street_name'])
    resale_price.append(hdb_price_dict_records[i]['resale_price'])
    month.append(hdb_price_dict_records[i]['month'])
    remaining_lease.append(hdb_price_dict_records[i]['remaining_lease'])
    lease_commence_date.append(hdb_price_dict_records[i]['lease_commence_date'])
    storey_range.append(hdb_price_dict_records[i]['storey_range'])
    _id.append(hdb_price_dict_records[i]['_id'])
    block.append(hdb_price_dict_records[i]['block'])

#create a pandas data frame to store all records
df_hdb_price = pd.DataFrame({
    'town': town,
    'flat_type': flat_type,
    'flat_model': flat_model,
    'floor_area_sqm': floor_area_sqm,
    'street_name': street_name,
    'resale_price': resale_price,
    'month': month,
    'remaining_lease': remaining_lease,
    'lease_commence_date': lease_commence_date,
    'storey_range': storey_range,
    '_id': _id,
    'block': block,
    'latitude': np.nan,
    'longitude': np.nan,
    'postal_code': np.nan
})

df_hdb_price['address'] = df_hdb_price['block'] + " " + df_hdb_price['street_name']
df_hdb_price.to_csv('raw_HDBresale2020.csv')
len(df_hdb_price)

77895

In [5]:
if rerun == True:
    latitude = []
    longitude = []
    postal_code = []
    
    for row in range(len(df_hdb_price)):
        #formulate query string  
        query_address = df_hdb_price['address'][row]
        query_string='https://developers.onemap.sg/commonapi/search?searchVal='+str(query_address)+'&returnGeom=Y&getAddrDetails=Y'
        resp = requests.get(query_string)
        
        try:
            data_geo_location = resp.json()
        
        except json.decoder.JSONDecodeError:
            latitude.append(0)
            longitude.append(0)
            postal_code.append(0)
            print('Could not decode a row')
            continue
        
        if data_geo_location['found'] != 0:
            latitude.append(data_geo_location['results'][0]['LATITUDE'])
            longitude.append(data_geo_location['results'][0]['LONGITUDE'])
            postal_code.append(data_geo_location['results'][0]['POSTAL'])
            print (str(query_address) + " ,Lat: " + data_geo_location['results'][0]['LATITUDE'] + " Long: " + data_geo_location['results'][0]['LONGITUDE'])
        else:
            latitude.append(0)
            longitude.append(0)
            postal_code.append(0)
            print ('no result')
            
    #export the full dataframe for hdb with longitude and latitudes into csv
    df_hdb_price['latitude'] = latitude
    df_hdb_price['longitude'] = longitude
    df_hdb_price['postal_code'] = postal_code

    df_hdb_price.to_csv('clean_HDBresale2020.csv')

406 ANG MO KIO AVE 10 ,Lat: 1.362004539 Long: 103.85387990000001
108 ANG MO KIO AVE 4 ,Lat: 1.370966352 Long: 103.83820190000002
602 ANG MO KIO AVE 5 ,Lat: 1.38070883 Long: 103.8353682
465 ANG MO KIO AVE 10 ,Lat: 1.3662010409999998 Long: 103.857201
601 ANG MO KIO AVE 5 ,Lat: 1.381041355 Long: 103.8351317
150 ANG MO KIO AVE 5 ,Lat: 1.376806785 Long: 103.84201800000001
447 ANG MO KIO AVE 10 ,Lat: 1.3674790140000002 Long: 103.8559671
218 ANG MO KIO AVE 1 ,Lat: 1.365119086 Long: 103.84174250000001
447 ANG MO KIO AVE 10 ,Lat: 1.3674790140000002 Long: 103.8559671
571 ANG MO KIO AVE 3 ,Lat: 1.3700550130000002 Long: 103.8548806
534 ANG MO KIO AVE 10 ,Lat: 1.3740584630000001 Long: 103.8541682
233 ANG MO KIO AVE 3 ,Lat: 1.36754925 Long: 103.8367406
235 ANG MO KIO AVE 3 ,Lat: 1.366823609 Long: 103.8364912
219 ANG MO KIO AVE 1 ,Lat: 1.36598198 Long: 103.840654
536 ANG MO KIO AVE 10 ,Lat: 1.374473785 Long: 103.8541005
230 ANG MO KIO AVE 3 ,Lat: 1.3688544519999999 Long: 103.8378964
570 ANG MO KIO AV

181 BISHAN ST 13 ,Lat: 1.349138096 Long: 103.8528785
260 BISHAN ST 22 ,Lat: 1.3596137680000002 Long: 103.8421874
275A BISHAN ST 24 ,Lat: 1.35673539 Long: 103.8435198
214 BISHAN ST 23 ,Lat: 1.357511897 Long: 103.8483034
182 BISHAN ST 13 ,Lat: 1.350205825 Long: 103.85304920000002
448 BRIGHT HILL DR ,Lat: 1.35840617 Long: 103.8314316
402 SIN MING AVE ,Lat: 1.362768866 Long: 103.8327589
128 BISHAN ST 12 ,Lat: 1.34608832 Long: 103.85046679999999
303 SHUNFU RD ,Lat: 1.349769429 Long: 103.8384765
275A BISHAN ST 24 ,Lat: 1.35673539 Long: 103.8435198
134 BISHAN ST 12 ,Lat: 1.345411048 Long: 103.8520798
342 BT BATOK ST 34 ,Lat: 1.362583231 Long: 103.74857490000001
530 BT BATOK ST 51 ,Lat: 1.3561819919999998 Long: 103.7510934
145 BT BATOK ST 11 ,Lat: 1.349973055 Long: 103.7437249
528 BT BATOK ST 51 ,Lat: 1.3566514680000001 Long: 103.7510918
537 BT BATOK ST 52 ,Lat: 1.355115164 Long: 103.7508779
213 BT BATOK ST 21 ,Lat: 1.346818455 Long: 103.7524969
219 BT BATOK ST 21 ,Lat: 1.347207298 Long: 103.7

418 FAJAR RD ,Lat: 1.384319661 Long: 103.76886590000001
484 SEGAR RD ,Lat: 1.38840059 Long: 103.77188220000001
140 PETIR RD ,Lat: 1.3755029909999998 Long: 103.7689524
152 GANGSA RD ,Lat: 1.375224695 Long: 103.7659225
537 BT PANJANG RING RD ,Lat: 1.3841162790000001 Long: 103.7628642
401 FAJAR RD ,Lat: 1.380554321 Long: 103.7687304
242 BT PANJANG RING RD ,Lat: 1.3800720880000001 Long: 103.7718336
613 BT PANJANG RING RD ,Lat: 1.384236786 Long: 103.7618809
654 SENJA RD ,Lat: 1.3875559309999999 Long: 103.7642821
536 JELAPANG RD ,Lat: 1.3842218309999998 Long: 103.76376690000001
154 GANGSA RD ,Lat: 1.374816801 Long: 103.7651093
154 GANGSA RD ,Lat: 1.374816801 Long: 103.7651093
154 GANGSA RD ,Lat: 1.374816801 Long: 103.7651093
174 LOMPANG RD ,Lat: 1.380215441 Long: 103.7663022
177 LOMPANG RD ,Lat: 1.380387125 Long: 103.7653546
606 SENJA RD ,Lat: 1.3812957469999998 Long: 103.7615713
650 SENJA LINK ,Lat: 1.38691071 Long: 103.7633102
228 PENDING RD ,Lat: 1.375346635 Long: 103.7709554
151 PETIR RD

623 HOUGANG AVE 8 ,Lat: 1.3705138730000002 Long: 103.8823235
311 HOUGANG AVE 5 ,Lat: 1.365667331 Long: 103.8948537
501 HOUGANG AVE 8 ,Lat: 1.372052696 Long: 103.8865314
698 HOUGANG ST 61 ,Lat: 1.37506139 Long: 103.8869105
698 HOUGANG ST 61 ,Lat: 1.37506139 Long: 103.8869105
307 HOUGANG AVE 5 ,Lat: 1.3666599940000002 Long: 103.8950097
21 HOUGANG AVE 3 ,Lat: 1.364245984 Long: 103.8914777
322 HOUGANG AVE 5 ,Lat: 1.367098554 Long: 103.8969787
308 HOUGANG AVE 5 ,Lat: 1.3668091080000002 Long: 103.895756
154 HOUGANG ST 11 ,Lat: 1.3522029530000002 Long: 103.8801732
339 HOUGANG AVE 7 ,Lat: 1.370025457 Long: 103.8985723
681 HOUGANG AVE 8 ,Lat: 1.372978403 Long: 103.8856792
314 HOUGANG AVE 5 ,Lat: 1.3647646519999999 Long: 103.89421879999999
336 HOUGANG AVE 7 ,Lat: 1.36930321 Long: 103.8983512
321 HOUGANG AVE 5 ,Lat: 1.367101312 Long: 103.898278
602 HOUGANG AVE 4 ,Lat: 1.371232979 Long: 103.88691800000001
83 C'WEALTH CL ,Lat: 1.304825696 Long: 103.80113730000001
709 HOUGANG AVE 2 ,Lat: 1.367061426

756 JURONG WEST ST 74 ,Lat: 1.3493267569999998 Long: 103.7007218
406 JURONG WEST ST 42 ,Lat: 1.354314355 Long: 103.72239590000001
430 JURONG WEST AVE 1 ,Lat: 1.3519543109999999 Long: 103.7256226
713 JURONG WEST ST 71 ,Lat: 1.3434009059999998 Long: 103.6962525
259 BOON LAY DR ,Lat: 1.3455143619999999 Long: 103.7086356
450 JURONG WEST ST 42 ,Lat: 1.351638892 Long: 103.71752409999999
722 JURONG WEST AVE 5 ,Lat: 1.343669447 Long: 103.6982983
540 JURONG WEST AVE 1 ,Lat: 1.350592139 Long: 103.7153486
452 JURONG WEST ST 42 ,Lat: 1.3515826919999998 Long: 103.7185162
648D JURONG WEST ST 61 ,Lat: 1.33943037 Long: 103.697684
988A JURONG WEST ST 93 ,Lat: 1.33648744 Long: 103.6956145
674B JURONG WEST ST 65 ,Lat: 1.3451337319999999 Long: 103.7020602
330 TAH CHING RD ,Lat: 1.337667461 Long: 103.7241548
655B JURONG WEST ST 61 ,Lat: 1.33550104 Long: 103.697514
682C JURONG WEST CTRL 1 ,Lat: 1.343152907 Long: 103.7053946
619 JURONG WEST ST 65 ,Lat: 1.3415173459999998 Long: 103.6998994
657A JURONG WEST ST

...

210 SERANGOON CTRL ,Lat: 1.354929782 Long: 103.87363990000001
206 SERANGOON CTRL ,Lat: 1.353475064 Long: 103.87339229999999
106 SERANGOON NTH AVE 1 ,Lat: 1.3702446209999999 Long: 103.870823
425 SERANGOON AVE 1 ,Lat: 1.348126435 Long: 103.87660509999999
403 SERANGOON AVE 1 ,Lat: 1.346483281 Long: 103.87249399999999
307 SERANGOON AVE 2 ,Lat: 1.354628177 Long: 103.8670687
331 SERANGOON AVE 3 ,Lat: 1.34964854 Long: 103.8702122
327 SERANGOON AVE 3 ,Lat: 1.3505992669999998 Long: 103.86851490000001
332 SERANGOON AVE 3 ,Lat: 1.351017195 Long: 103.87018509999999
227 SERANGOON AVE 4 ,Lat: 1.356470981 Long: 103.8711268
224 SERANGOON AVE 4 ,Lat: 1.35720575 Long: 103.87083129999999
419 SERANGOON CTRL ,Lat: 1.34920192 Long: 103.8758597
416 SERANGOON CTRL ,Lat: 1.350205615 Long: 103.8748185
255 SERANGOON CTRL DR ,Lat: 1.355062011 Long: 103.8708719
144 SERANGOON NTH AVE 1 ,Lat: 1.367781392 Long: 103.8730413
111 SERANGOON NTH AVE 1 ,Lat: 1.369047313 Long: 103.870584
101 SERANGOON NTH AVE 1 ,Lat: 1.3710

497B TAMPINES ST 45 ,Lat: 1.3586829969999998 Long: 103.9580245
741 TAMPINES ST 72 ,Lat: 1.3600117840000001 Long: 103.9330438
742 TAMPINES ST 72 ,Lat: 1.3595887480000002 Long: 103.933361
887 TAMPINES ST 81 ,Lat: 1.350141948 Long: 103.93147420000001
888A TAMPINES ST 81 ,Lat: 1.35048495 Long: 103.9309126
842B TAMPINES ST 82 ,Lat: 1.35132562 Long: 103.93692109999999
867 TAMPINES ST 83 ,Lat: 1.35511312 Long: 103.9340464
864A TAMPINES ST 83 ,Lat: 1.354684946 Long: 103.93573719999999
833 TAMPINES ST 83 ,Lat: 1.350689363 Long: 103.9339915
886 TAMPINES ST 83 ,Lat: 1.351048571 Long: 103.9320571
843 TAMPINES ST 83 ,Lat: 1.351879216 Long: 103.9346909
868 TAMPINES ST 83 ,Lat: 1.354776164 Long: 103.9339796
883 TAMPINES ST 84 ,Lat: 1.35185623 Long: 103.932939
873 TAMPINES ST 84 ,Lat: 1.353945406 Long: 103.93219870000001
930 TAMPINES ST 91 ,Lat: 1.34596292 Long: 103.93961479999999
931 TAMPINES ST 91 ,Lat: 1.3458725980000001 Long: 103.93910720000001
155 SIMEI RD ,Lat: 1.3446994509999999 Long: 103.95821

139B LOR 1A TOA PAYOH ,Lat: 1.336711091 Long: 103.8438782
121 LOR 2 TOA PAYOH ,Lat: 1.339162623 Long: 103.8462435
81A LOR 4 TOA PAYOH ,Lat: 1.335658357 Long: 103.85007759999999
44 LOR 5 TOA PAYOH ,Lat: 1.336231496 Long: 103.8540431
14A LOR 7 TOA PAYOH ,Lat: 1.336268211 Long: 103.8583152
218 LOR 8 TOA PAYOH ,Lat: 1.342725835 Long: 103.8551516
223 LOR 8 TOA PAYOH ,Lat: 1.341264797 Long: 103.8555528
215 LOR 8 TOA PAYOH ,Lat: 1.341828137 Long: 103.85510790000001
224 LOR 8 TOA PAYOH ,Lat: 1.341176079 Long: 103.8560662
20 JOO SENG RD ,Lat: 1.334057601 Long: 103.8813662
240 LOR 1 TOA PAYOH ,Lat: 1.340876446 Long: 103.85083
101B LOR 2 TOA PAYOH ,Lat: 1.339598845 Long: 103.8476054
131 POTONG PASIR AVE 1 ,Lat: 1.3343832709999999 Long: 103.8653121
780F WOODLANDS CRES ,Lat: 1.447777265 Long: 103.8011484
780F WOODLANDS CRES ,Lat: 1.447777265 Long: 103.8011484
780B WOODLANDS CRES ,Lat: 1.44894246 Long: 103.8010163
30 MARSILING DR ,Lat: 1.442559074 Long: 103.7724055
1 MARSILING DR ,Lat: 1.440671099 L

880 WOODLANDS ST 82 ,Lat: 1.444489684 Long: 103.79264309999999
839 WOODLANDS ST 82 ,Lat: 1.44272214 Long: 103.7917313
141 MARSILING RD ,Lat: 1.4373687 Long: 103.7770722
134 MARSILING RD ,Lat: 1.436637071 Long: 103.77739759999999
308 WOODLANDS AVE 1 ,Lat: 1.429804224 Long: 103.7765607
340 WOODLANDS AVE 1 ,Lat: 1.4311642480000002 Long: 103.78113470000001
340 WOODLANDS AVE 1 ,Lat: 1.4311642480000002 Long: 103.78113470000001
358 WOODLANDS AVE 5 ,Lat: 1.4336826269999998 Long: 103.78387509999999
356 WOODLANDS AVE 5 ,Lat: 1.433275633 Long: 103.7849719
533 WOODLANDS DR 14 ,Lat: 1.430548515 Long: 103.79207209999998
583 WOODLANDS DR 16 ,Lat: 1.430395887 Long: 103.7953168
587 WOODLANDS DR 16 ,Lat: 1.428446579 Long: 103.7952889
893A WOODLANDS DR 50 ,Lat: 1.4368443119999998 Long: 103.79061309999999
636 WOODLANDS RING RD ,Lat: 1.436864723 Long: 103.8027013
176 WOODLANDS ST 13 ,Lat: 1.4335785840000002 Long: 103.77835350000001
323 WOODLANDS ST 32 ,Lat: 1.4311727490000001 Long: 103.7791132
403 WOODLAND

760 YISHUN ST 72 ,Lat: 1.425794855 Long: 103.8327247
873 YISHUN ST 81 ,Lat: 1.414694801 Long: 103.8369503
879 YISHUN ST 81 ,Lat: 1.414441679 Long: 103.8361178
852 YISHUN ST 81 ,Lat: 1.4160596019999998 Long: 103.8367958
867 YISHUN ST 81 ,Lat: 1.413906055 Long: 103.8380052
432C YISHUN AVE 1 ,Lat: 1.4194957019999999 Long: 103.8459734
432C YISHUN AVE 1 ,Lat: 1.4194957019999999 Long: 103.8459734
432B YISHUN AVE 1 ,Lat: 1.4190999340000001 Long: 103.8464618
432B YISHUN AVE 1 ,Lat: 1.4190999340000001 Long: 103.8464618
428A YISHUN AVE 11 ,Lat: 1.422527792 Long: 103.84744520000001
426D YISHUN AVE 11 ,Lat: 1.423122016 Long: 103.8474982
426D YISHUN AVE 11 ,Lat: 1.423122016 Long: 103.8474982
864 YISHUN AVE 4 ,Lat: 1.416672578 Long: 103.8392423
863 YISHUN AVE 4 ,Lat: 1.416939516 Long: 103.8386199
733 YISHUN AVE 5 ,Lat: 1.429654211 Long: 103.8308899
172 YISHUN AVE 7 ,Lat: 1.43660111 Long: 103.831091
175 YISHUN AVE 7 ,Lat: 1.4376032140000001 Long: 103.83246820000001
317A YISHUN AVE 9 ,Lat: 1.434505929

In [22]:
HDB2020_coords = pd.read_csv("clean_HDBresale2020.csv")

# deleted all invalid entries
HDB2020_coords.drop(HDB2020_coords[(HDB2020_coords.latitude == 0)].index, 
                    inplace = True)

HDB2020_coords

Unnamed: 0        town         flat_type        flat_model  \
0               0  ANG MO KIO            2 ROOM          Improved   
1               1  ANG MO KIO            3 ROOM    New Generation   
2               2  ANG MO KIO            3 ROOM    New Generation   
3               3  ANG MO KIO            3 ROOM    New Generation   
4               4  ANG MO KIO            3 ROOM    New Generation   
...           ...         ...               ...               ...   
77890       77890      YISHUN         EXECUTIVE        Maisonette   
77891       77891      YISHUN         EXECUTIVE         Apartment   
77892       77892      YISHUN         EXECUTIVE         Apartment   
77893       77893      YISHUN         EXECUTIVE        Maisonette   
77894       77894      YISHUN  MULTI-GENERATION  Multi Generation   

       floor_area_sqm        street_name  resale_price    month  \
0                44.0  ANG MO KIO AVE 10      232000.0  2017-01   
1                67.0   ANG MO KIO AVE 4      250000.0  2017-01   
2                67.0   ANG MO KIO AVE 5      262000.0  2017-01   
3                68.0  ANG MO KIO AVE 10      265000.0  2017-01   
4                67.0   ANG MO KIO AVE 5      265000.0  2017-01   
...               ...                ...           ...      ...   
77890           146.0       YISHUN ST 61      598000.0  2020-08   
77891           142.0       YISHUN ST 61      510000.0  2020-08   
77892           142.0       YISHUN ST 71      555000.0  2020-08   
77893           145.0       YISHUN ST 81      639888.0  2020-08   
77894           164.0       YISHUN AVE 4      725000.0  2020-08   

          remaining_lease  lease_commence_date storey_range    _id block  \
0      61 years 04 months                 1979     10 TO 12      1   406   
1      60 years 07 months                 1978     01 TO 03      2   108   
2      62 years 05 months                 1980     01 TO 03      3   602   
3       62 years 01 month                 1980     04 TO 06      4   465   
4      62 years 05 months                 1980     01 TO 03      5   601   
...                   ...                  ...          ...    ...   ...   
77890  66 years 03 months                 1987     04 TO 06  77891   611   
77891   66 years 01 month                 1987     01 TO 03  77892   643   
77892  64 years 11 months                 1986     07 TO 09  77893   724   
77893  66 years 04 months                 1987     04 TO 06  77894   877   
77894  66 years 04 months                 1987     01 TO 03  77895   666   

       latitude   longitude postal_code                address  
0      1.362005  103.853880      560406  406 ANG MO KIO AVE 10  
1      1.370966  103.838202      560108   108 ANG MO KIO AVE 4  
2      1.380709  103.835368      560602   602 ANG MO KIO AVE 5  
3      1.366201  103.857201      560465  465 ANG MO KIO AVE 10  
4      1.381041  103.835132      560601   601 ANG MO KIO AVE 5  
...         ...         ...         ...                    ...  
77890  1.420201  103.836153      760611       611 YISHUN ST 61  
77891  1.421335  103.837437      760643       643 YISHUN ST 61  
77892  1.426475  103.829916      760724       724 YISHUN ST 71  
77893  1.413902  103.835454      760877       877 YISHUN ST 81  
77894  1.418998  103.840568      760666       666 YISHUN AVE 4  

[77717 rows x 17 columns]

### MRT Coordinates<a id="subsection2.2"></a>

In [7]:
MRT_coords = pd.read_csv("clean_MRT.csv")

MRT_coords

OBJECTID                     STN_NAME STN_NO           X           Y  \
0          12        ADMIRALTY MRT STATION   NS10  24402.1063  46918.1131   
1          16         ALJUNIED MRT STATION    EW9  33518.6049  33190.0020   
2          33       ANG MO KIO MRT STATION   NS16  29807.2655  39105.7720   
3          81            BAKAU LRT STATION    SE3  36026.0821  41113.8766   
4          80          BANGKIT LRT STATION    BP9  21248.2460  40220.9693   
..        ...                          ...    ...         ...         ...   
182       175  WOODLANDS SOUTH MRT STATION    TE3  23607.8309  45444.7113   
183       146        WOODLEIGH MRT STATION   NE11  32173.3186  35706.3794   
184         6          YEW TEE MRT STATION    NS5  18438.9791  42158.0124   
185        41     YIO CHU KANG MRT STATION   NS15  29294.1283  40413.0820   
186        13           YISHUN MRT STATION   NS13  28187.6787  45686.0701   

     Latitude   Longitude   COLOR  
0    1.440585  103.800998     RED  
1    1.316433  103.882893   GREEN  
2    1.369933  103.849553     RED  
3    1.388093  103.905418  OTHERS  
4    1.380018  103.772667  OTHERS  
..        ...         ...     ...  
182  1.427260  103.793863  OTHERS  
183  1.339190  103.870808  PURPLE  
184  1.397535  103.747431     RED  
185  1.381756  103.844944     RED  
186  1.429443  103.835005     RED  

[187 rows x 8 columns]

### Mall Coordinates<a id="subsection2.3"></a>

In [8]:
list_of_shopping_mall = [
    '100 AM', '313@Somerset', 'Aperia', 'Balestier Hill Shopping Centre', 'Bugis Cube', 
    'Bugis Junction', 'Bugis+', 'Capitol Piazza', 'Cathay Cineleisure Orchard', 'City Gate', 
    'City Square Mall', 'CityLink Mall', 'Clarke Quay Central', 'Duo', 'Far East Plaza', 'Funan', 
    'Great World City', 'HDB Hub', 'Holland Village Shopping Mall', 'ION Orchard', 'Junction 8', 
    'Knightsbridge[1]', 'Liang Court', 'Liat Towers', 'Lucky Plaza', 'Marina Bay Financial Centre Tower 3', 
    'Marina Bay Link Mall', 'Marina Bay Sands', 'Marina One', 'Marina Square', 'Midpoint Orchard', 'Millenia Walk', 
    'Mustafa Shopping Centre', 'Ngee Ann City', 'Orchard Central', 'Orchard Gateway', 'Orchard Plaza', 
    'Orchard Shopping Centre', 'Palais Renaissance', 'Peoples Park Centre', 'Peoples Park Complex', 
    'Plaza Singapura', 'PoMo', 'Raffles City', 'Scotts Square', 'Serangoon Plaza', 'Shaw House and Centre', 
    'Sim Lim Square', 'Singapore Shopping Centre', 'Square 2', 'Suntec City', 'Tanglin Mall', 'Tangs', 
    'Tanjong Pagar Centre', 'Tekka Centre', 'The Centrepoint', 'The Paragon', 'The Poiz [2]', 
    'The Shoppes at Marina Bay Sands', 'The South Beach', 'Thomson Plaza', 'United Square, The Kids Learning Mall', 
    'Velocity', 'Wheelock Place', 'Wisma Atria', 'Zhongshan Mall', '112 Katong', 'Bedok Mall', 'Bedok Point', 
    'Century Square', 'Changi Airport', 'Changi City Point', 'City Plaza', 'Djitsun Mall Bedok', 'Downtown East', 
    'East Village', 'Eastpoint Mall', 'Elias Mall', 'Kallang Wave Mall', 'Katong Square', 'Katong V', 
    'Kinex', 'Leisure Park Kallang', 'Loyang Point', 'Our Tampines Hub', 'Parkway Parade', 
    'Paya Lebar Square', 'PLQ Mall', 'Singapore Post Centre', 'Tampines 1', 'Tampines Mall', 'The Flow', 
    'White Sands', '888 Plaza', 'Admiralty Place', 'AMK Hub', 'Beauty World Centre', 'Beauty World Plaza', 
    'Broadway Plaza', 'Buangkok Square', 'Bukit Panjang Plaza', 'Bukit Timah Plaza', 'Causeway Point', 
    'Compass One', 'Djitsun Mall', 'Fajar Shopping Centre', 'Greenridge Shopping Centre', 'Greenwich V', 
    'Heartland Mall', 'Hillion Mall', 'HillV2', 'Hougang 1', 'Hougang Green Shopping Mall', 'Hougang Mall', 
    'Jubilee Square', 'Junction 10', 'Junction 9', 'Keat Hong Shopping Centre', 'KKH The Retail Mall', 
    'Limbang Shopping Centre', 'Lot One', 'Marsiling Mall', 'myVillage @ Serangoon', 'NEX', 'North East', 
    'North West', 'Northpoint City', 'Oasis Terraces', 'Punggol Plaza', 'Rail Mall', 'Rivervale Mall', 
    'Rivervale Plaza', 'Sembawang Shopping Centre', 'Sun Plaza', 'Sunshine Place', 'Teck Whye Shopping Centre', 
    'The Midtown', 'The Seletar Mall', 'Upper Serangoon Shopping Centre', 'Waterway Point', 'West Mall', 
    'Wisteria Mall', 'Woodlands Mart', 'Yew Tee Point', 'Yew Tee Shopping Centre', 'Yew Tee Square', 
    'Alexandra Retail Centre', 'HarbourFront Centre', 'VivoCity', '321 Clementi', 'Alexandra Central', 
    'Anchorpoint', 'Big Box', 'Boon Lay Shopping Centre', 'Fairprice Hub', 'Gek Poh Shopping Centre', 
    'Grantral Mall', 'IMM', 'JCube', 'Jem', 'Jurong Point', 'OD Mall', 'Pioneer Mall', 'Queensway Shopping Centre', 
    'Rochester Mall', 'Taman Jurong Shopping Centre', 'The Clementi Mall', 'The Star Vista', 'Tiong Bahru Plaza', 
    'West Coast Plaza', 'Westgate Mall',
]

len(list_of_shopping_mall)

171

In [12]:
if rerun == True:
    mall_name = []
    mall_roadname = []
    mall_lat = []
    mall_long = []
    
    for i in range(0, len(list_of_shopping_mall)):
        query_address = list_of_shopping_mall[i]
        query_string = 'https://developers.onemap.sg/commonapi/search?searchVal='+str(query_address)+'&returnGeom=Y&getAddrDetails=Y'
        resp = requests.get(query_string)
        try:
            data_mall = json.loads(resp.content)
        except json.decoder.JSONDecodeError:
            print('Could not decode a row')
            continue
    
        if data_mall['found'] != 0:
            mall_name.append(query_address)
            mall_roadname.append(data_mall["results"][0]["ROAD_NAME"])
            mall_lat.append(data_mall["results"][0]["LATITUDE"])
            mall_long.append(data_mall["results"][0]["LONGITUDE"])

            print (str(query_address)+" ,Lat: "+data_mall['results'][0]['LATITUDE'] +" Long: "+data_mall['results'][0]['LONGITUDE'])

        else:
            print ("No Results")

    # Store this information in a dataframe
    df_Malls = pd.DataFrame({
        'Mall': mall_name,
        'RoadName': mall_roadname,
        'Latitude': mall_lat,
        'Longitude': mall_long
    })

    df_Malls.to_csv('clean_Mall.csv')

Mall_coords = pd.read_csv('clean_Mall.csv')

Mall_coords

100 AM ,Lat: 1.2745882179999999 Long: 103.84347070000001
313@Somerset ,Lat: 1.3010065690000001 Long: 103.83824659999999
Aperia ,Lat: 1.30974242 Long: 103.8641016
Balestier Hill Shopping Centre ,Lat: 1.326124169 Long: 103.8437095
Bugis Cube ,Lat: 1.298195005 Long: 103.85565550000001
Bugis Junction ,Lat: 1.300117893 Long: 103.8561916
Bugis+ ,Lat: 1.300007152 Long: 103.8556805
Capitol Piazza ,Lat: 1.293063359 Long: 103.85129350000001
Cathay Cineleisure Orchard ,Lat: 1.301497434 Long: 103.8364448
City Gate ,Lat: 1.302347543 Long: 103.86225999999999
City Square Mall ,Lat: 1.31147745 Long: 103.8567808
CityLink Mall ,Lat: 1.292378607 Long: 103.854663
No Results
Duo ,Lat: 1.299216621 Long: 103.8579968
Far East Plaza ,Lat: 1.3073111259999999 Long: 103.83394
Funan ,Lat: 1.2912440059999999 Long: 103.8499848
Great World City ,Lat: 1.293154929 Long: 103.831928
HDB Hub ,Lat: 1.33218812 Long: 103.8470778
No Results
ION Orchard ,Lat: 1.3040425340000001 Long: 103.83188829999999
Junction 8 ,Lat: 1.35017

Queensway Shopping Centre ,Lat: 1.287617926 Long: 103.8033911
Rochester Mall ,Lat: 1.3054076559999999 Long: 103.78844670000001
Taman Jurong Shopping Centre ,Lat: 1.334844875 Long: 103.720462
The Clementi Mall ,Lat: 1.315496754 Long: 103.76457020000001
The Star Vista ,Lat: 1.30697044 Long: 103.7884203
Tiong Bahru Plaza ,Lat: 1.2864712 Long: 103.8271583
West Coast Plaza ,Lat: 1.303742583 Long: 103.7660929
No Results


Unnamed: 0                            Mall                  RoadName  \
0             0                          100 AM               TRAS STREET   
1             1                    313@Somerset              ORCHARD ROAD   
2             2                          Aperia            KALLANG AVENUE   
3             3  Balestier Hill Shopping Centre            BALESTIER ROAD   
4             4                      Bugis Cube         NORTH BRIDGE ROAD   
..          ...                             ...                       ...   
151         151    Taman Jurong Shopping Centre           YUNG SHENG ROAD   
152         152               The Clementi Mall  COMMONWEALTH AVENUE WEST   
153         153                  The Star Vista      VISTA EXCHANGE GREEN   
154         154               Tiong Bahru Plaza          TIONG BAHRU ROAD   
155         155                West Coast Plaza           WEST COAST ROAD   

     Latitude   Longitude  
0    1.274588  103.843471  
1    1.301007  103.838247  
2    1.309742  103.864102  
3    1.326124  103.843710  
4    1.298195  103.855655  
..        ...         ...  
151  1.334845  103.720462  
152  1.315497  103.764570  
153  1.306970  103.788420  
154  1.286471  103.827158  
155  1.303743  103.766093  

[156 rows x 5 columns]

### BusStop Coordinates<a id="subsection2.4"></a>

In [10]:
Bus_coords = pd.read_csv('clean_bus.csv')

Bus_coords

Busstop_no.  Latitude   Longitude
0           10009  1.282102  103.817225
1           10011  1.277738  103.837497
2           10017  1.278320  103.837626
3           10018  1.279008  103.838604
4           10021  1.277448  103.838389
...           ...       ...         ...
4988         3419  1.271277  103.862977
4989         3421  1.266941  103.859648
4990         3411  1.271593  103.863009
4991         3339  1.274985  103.859500
4992         5009  1.285926  103.849236

[4993 rows x 3 columns]

### Import All Other Relevant Datasets<a id="subsection2.5"></a>

## General Functions<a id="section3"></a>

In [11]:
#calculate distance between two pairs of lat and long
def distance(x1,y1,x2,y2):
    R = 6373.0
    lat1 = radians(x1)
    lon1 = radians(y1)
    lat2 = radians(x2)
    lon2 = radians(y2)
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = (sin(dlat/2))**2 + cos(lat1)*cos(lat2)*(sin(dlon/2))**2
    c = 2* atan2(sqrt(a), sqrt(1-a))
    dist = R * c
    return dist